# Nonlinear Elasticity

In [ ]:
from ngsolve import *
from ngsolve.webgui import Draw

a rectangle with refinement at corners:

In [ ]:
from netgen.occ import *
shape = Rectangle(1,0.1).Face()
shape.edges.Max(X).name="right"
shape.edges.Min(X).name="left"
shape.edges.Max(Y).name="top"
shape.edges.Min(Y).name="bot"
shape.vertices.Min(X+Y).maxh=0.01
shape.vertices.Min(X-Y).maxh=0.01
mesh = Mesh(OCCGeometry(shape, dim=2).GenerateMesh(maxh=0.05))

Cauchy-Green tensor

$$
C = F^T F \qquad \text{with} \qquad F = I + \nabla u
$$

and hyperelastic energy density

$$
W : {\mathbb R}^{d \times d, sym} \rightarrow {\mathbb R}
$$

In [ ]:
E, nu = 210, 0.2
mu  = E / 2 / (1+nu)
lam = E * nu / ((1+nu)*(1-2*nu))

def C(u):
    F = Id(2) + Grad(u)
    return F.trans * F

def NeoHooke (C):
    return 0.5*mu*(Trace(C-Id(2)) + 2*mu/lam*Det(C)**(-lam/2/mu)-1)

stationary point of total energy:

$$
\delta \int W(C(u)) - f u = 0
$$

In [ ]:
factor = Parameter(0)
force = CoefficientFunction( (0,factor) )

fes = H1(mesh, order=4, dirichlet="left", dim=mesh.dim)
u  = fes.TrialFunction()

a = BilinearForm(fes, symmetric=True)
a += Variation(NeoHooke(C(u)).Compile()*dx)
a += Variation((-InnerProduct(force,u)).Compile()*dx)

gfu = GridFunction(fes)
gfu.vec[:] = 0

a simple Newton solver, using automatic differentiation for residual and tangential stiffness:

In [ ]:
def SolveNewton(printrates=False):
    for it in range(10):
        if (printrates):
            print ("it", it, "energy = ", a.Energy(gfu.vec))
        res = a.Apply(gfu.vec)
        a.AssembleLinearization(gfu.vec)
        inv = a.mat.Inverse(fes.FreeDofs() ) 
        gfu.vec.data -= inv*res

In [ ]:
factor.Set(0.4)
SolveNewton(printrates=True)
scene = Draw (C(gfu)[0,0]-1, mesh, deformation=gfu, min=-0.1, max=0.1, center=(0.5,0.5))

In [ ]:
numsteps = 5
maxload = 2

for ls in range (numsteps):
    factor.Set(maxload*(ls+1)/numsteps)
    SolveNewton()
    Draw (C(gfu)[0,0]-1, mesh, deformation=gfu, min=-0.2, max=0.2)

## Stress tensor

Compute $2^{nd}$ Piola Kirchhoff stress tensor by symbolic differentiation:

$$
\Sigma_{i,j} = \frac{\partial W}{\partial C_{i,j}} (C)
$$

In [ ]:
C_=C(gfu).MakeVariable()
sigma = NeoHooke(C_).Diff(C_)

Draw (sigma[0,0], mesh, "Sxx", deformation=gfu, min=-10.001, max=10.001); 

The energy functional is represented as an expression tree:

In [ ]:
u  = fes.TrialFunction()
print (NeoHooke(C(u)))

With the `Compile` method, the tree is linearized, and common sub-expressions are merged:

In [ ]:
print (NeoHooke(C(u)).Compile())

We can also *real*-compile, what means we generate C++ code, and send it through the compiler

In [ ]:
ngsglobals.msg_level=3
NeoHooke(C(u)).Compile(realcompile=True, wait=True, keep_files=True);

The generated code:

```cpp
#include<fem.hpp>
#if defined(__GNUC__) || defined(__clang__)
#pragma GCC diagnostic ignored "-Wunused-but-set-variable"
#endif
using namespace ngfem;
extern "C" {
  extern "C" void* compiled_code_pointer48;
  extern "C" void* compiled_code_pointer49;
  extern "C" void* compiled_code_pointer50;
  extern "C" void* compiled_code_pointer51;
  extern "C" void* compiled_code_pointer52;
  extern "C" void* compiled_code_pointer53;
  void CompiledEvaluate(BaseMappedIntegrationRule & mir, BareSliceMatrix<double> results ) {

    FlatMatrix<double> values_1;
    ProxyUserData * tmp_1_0 = (ProxyUserData*)mir.GetTransformation().userdata;
    {
      if (tmp_1_0->fel) {
        auto x = tmp_1_0->GetMemory (reinterpret_cast<ProxyFunction*>(compiled_code_pointer48));
        values_1.AssignMemory(x.Height(), x.Width(), &x(0,0));
      }
    }
    [[maybe_unused]] const bool has_values_1 = tmp_1_0->HasMemory(reinterpret_cast<ProxyFunction*>(compiled_code_pointer48));
    double comp_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==0 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer48))
      comp_1_0_0 = 1.0;
    double comp_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==1 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer48))
      comp_1_0_1 = 1.0;
    double comp_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==2 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer48))
      comp_1_1_0 = 1.0;
    double comp_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==3 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer48))
      comp_1_1_1 = 1.0;

    [[maybe_unused]] auto points = mir.GetPoints();
    [[maybe_unused]] auto domain_index = mir.GetTransformation().GetElementIndex();
    for ( auto i : Range(mir)) {
      [[maybe_unused]] auto & ip = mir[i];
      // step 0: Identity matrix
      double var_0_0_0;
      double var_0_0_1;
      double var_0_1_0;
      double var_0_1_1;
      var_0_0_0 = 1.0;
      var_0_0_1 = 0.0;
      var_0_1_0 = 0.0;
      var_0_1_1 = 1.0;
      // step 1: trial-function diffop = grad
      double var_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_0 = 0.0;
      double var_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_1 = 0.0;
      double var_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_0 = 0.0;
      double var_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_1 = 0.0;
      if (has_values_1) {
        var_1_0_0 = values_1(i,0);
        var_1_0_1 = values_1(i,1);
        var_1_1_0 = values_1(i,2);
        var_1_1_1 = values_1(i,3);
      } 
      // step 2: binary operation '+'
      double var_2_0_0;
      double var_2_0_1;
      double var_2_1_0;
      double var_2_1_1;
      var_2_0_0 = var_0_0_0 + var_1_0_0;
      var_2_0_1 = var_0_0_1 + var_1_0_1;
      var_2_1_0 = var_0_1_0 + var_1_1_0;
      var_2_1_1 = var_0_1_1 + var_1_1_1;
      // step 3: Matrix transpose
      double var_3_0_0;
      double var_3_0_1;
      double var_3_1_0;
      double var_3_1_1;
      var_3_0_0 = var_2_0_0;
      var_3_0_1 = var_2_1_0;
      var_3_1_0 = var_2_0_1;
      var_3_1_1 = var_2_1_1;
      // step 4: matrix-matrix multiply
      double var_4_0_0;
      double var_4_0_1;
      double var_4_1_0;
      double var_4_1_1;
      var_4_0_0 = (((var_3_0_0 * var_2_0_0)) + (var_3_0_1 * var_2_1_0));
      var_4_0_1 = (((var_3_0_0 * var_2_0_1)) + (var_3_0_1 * var_2_1_1));
      var_4_1_0 = (((var_3_1_0 * var_2_0_0)) + (var_3_1_1 * var_2_1_0));
      var_4_1_1 = (((var_3_1_0 * var_2_0_1)) + (var_3_1_1 * var_2_1_1));
      // step 5: Identity matrix
      double var_5_0_0;
      double var_5_0_1;
      double var_5_1_0;
      double var_5_1_1;
      var_5_0_0 = 1.0;
      var_5_0_1 = 0.0;
      var_5_1_0 = 0.0;
      var_5_1_1 = 1.0;
      // step 6: binary operation '-'
      double var_6_0_0;
      double var_6_0_1;
      double var_6_1_0;
      double var_6_1_1;
      var_6_0_0 = var_4_0_0 - var_5_0_0;
      var_6_0_1 = var_4_0_1 - var_5_0_1;
      var_6_1_0 = var_4_1_0 - var_5_1_0;
      var_6_1_1 = var_4_1_1 - var_5_1_1;
      // step 7: trace
      double var_7;
      var_7 = ((var_6_0_0) + var_6_1_1);
      // step 8: Determinant
      Mat<2,2,double> mat_8;
      mat_8(0,0) = var_2_0_0;
      mat_8(0,1) = var_2_0_1;
      mat_8(1,0) = var_2_1_0;
      mat_8(1,1) = var_2_1_1;
      double var_8;
      var_8 = Det(mat_8);
      // step 9: binary operation '*'
      double var_9;
      var_9 = var_8 * var_8;
      // step 10: -0.333333
      double var_10;
      var_10 = -0x1.5555555555556p-2 /* (-3.3333333333333337e-01) */;
      // step 11: binary operation 'pow'
      double var_11;
      var_11 = pow(var_9,var_10);
      // step 12: scale 3
      double var_12;
      var_12 = (0x1.8p+1 /* (3.0000000000000000e+00) */ * var_11);
      // step 13: binary operation '+'
      double var_13;
      var_13 = var_7 + var_12;
      // step 14: 1
      double var_14;
      var_14 = 0x1p+0 /* (1.0000000000000000e+00) */;
      // step 15: binary operation '-'
      double var_15;
      var_15 = var_13 - var_14;
      // step 16: scale 43.75
      double var_16;
      var_16 = (0x1.5ep+5 /* (4.3750000000000000e+01) */ * var_15);
      double var_17;
      var_17 = var_16;
      results(i,0) =var_17;

    }
  }

  void CompiledEvaluateSIMD(SIMD_BaseMappedIntegrationRule & mir, BareSliceMatrix<SIMD<double>> results ) {

    FlatMatrix<SIMD<double>> values_1;
    ProxyUserData * tmp_1_0 = (ProxyUserData*)mir.GetTransformation().userdata;
    {
      if (tmp_1_0->fel) {
        auto x = tmp_1_0->GetAMemory (reinterpret_cast<ProxyFunction*>(compiled_code_pointer49));
        values_1.AssignMemory(x.Height(), x.Width(), &x(0,0));
      }
    }
    [[maybe_unused]] const bool has_values_1 = tmp_1_0->HasMemory(reinterpret_cast<ProxyFunction*>(compiled_code_pointer49));
    SIMD<double> comp_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==0 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer49))
      comp_1_0_0 = 1.0;
    SIMD<double> comp_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==1 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer49))
      comp_1_0_1 = 1.0;
    SIMD<double> comp_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==2 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer49))
      comp_1_1_0 = 1.0;
    SIMD<double> comp_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==3 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer49))
      comp_1_1_1 = 1.0;

    [[maybe_unused]] auto points = mir.GetPoints();
    [[maybe_unused]] auto domain_index = mir.GetTransformation().GetElementIndex();
    for ( auto i : Range(mir)) {
      [[maybe_unused]] auto & ip = mir[i];
      // step 0: Identity matrix
      SIMD<double> var_0_0_0;
      SIMD<double> var_0_0_1;
      SIMD<double> var_0_1_0;
      SIMD<double> var_0_1_1;
      var_0_0_0 = 1.0;
      var_0_0_1 = 0.0;
      var_0_1_0 = 0.0;
      var_0_1_1 = 1.0;
      // step 1: trial-function diffop = grad
      SIMD<double> var_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_0 = 0.0;
      SIMD<double> var_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_1 = 0.0;
      SIMD<double> var_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_0 = 0.0;
      SIMD<double> var_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_1 = 0.0;
      // if (tmp_1_0->fel) {
      if (has_values_1) {
        var_1_0_0 = values_1(0,i);
        var_1_0_1 = values_1(1,i);
        var_1_1_0 = values_1(2,i);
        var_1_1_1 = values_1(3,i);
      }
      // step 2: binary operation '+'
      SIMD<double> var_2_0_0;
      SIMD<double> var_2_0_1;
      SIMD<double> var_2_1_0;
      SIMD<double> var_2_1_1;
      var_2_0_0 = var_0_0_0 + var_1_0_0;
      var_2_0_1 = var_0_0_1 + var_1_0_1;
      var_2_1_0 = var_0_1_0 + var_1_1_0;
      var_2_1_1 = var_0_1_1 + var_1_1_1;
      // step 3: Matrix transpose
      SIMD<double> var_3_0_0;
      SIMD<double> var_3_0_1;
      SIMD<double> var_3_1_0;
      SIMD<double> var_3_1_1;
      var_3_0_0 = var_2_0_0;
      var_3_0_1 = var_2_1_0;
      var_3_1_0 = var_2_0_1;
      var_3_1_1 = var_2_1_1;
      // step 4: matrix-matrix multiply
      SIMD<double> var_4_0_0;
      SIMD<double> var_4_0_1;
      SIMD<double> var_4_1_0;
      SIMD<double> var_4_1_1;
      var_4_0_0 = (((var_3_0_0 * var_2_0_0)) + (var_3_0_1 * var_2_1_0));
      var_4_0_1 = (((var_3_0_0 * var_2_0_1)) + (var_3_0_1 * var_2_1_1));
      var_4_1_0 = (((var_3_1_0 * var_2_0_0)) + (var_3_1_1 * var_2_1_0));
      var_4_1_1 = (((var_3_1_0 * var_2_0_1)) + (var_3_1_1 * var_2_1_1));
      // step 5: Identity matrix
      SIMD<double> var_5_0_0;
      SIMD<double> var_5_0_1;
      SIMD<double> var_5_1_0;
      SIMD<double> var_5_1_1;
      var_5_0_0 = 1.0;
      var_5_0_1 = 0.0;
      var_5_1_0 = 0.0;
      var_5_1_1 = 1.0;
      // step 6: binary operation '-'
      SIMD<double> var_6_0_0;
      SIMD<double> var_6_0_1;
      SIMD<double> var_6_1_0;
      SIMD<double> var_6_1_1;
      var_6_0_0 = var_4_0_0 - var_5_0_0;
      var_6_0_1 = var_4_0_1 - var_5_0_1;
      var_6_1_0 = var_4_1_0 - var_5_1_0;
      var_6_1_1 = var_4_1_1 - var_5_1_1;
      // step 7: trace
      SIMD<double> var_7;
      var_7 = ((var_6_0_0) + var_6_1_1);
      // step 8: Determinant
      Mat<2,2,SIMD<double>> mat_8;
      mat_8(0,0) = var_2_0_0;
      mat_8(0,1) = var_2_0_1;
      mat_8(1,0) = var_2_1_0;
      mat_8(1,1) = var_2_1_1;
      SIMD<double> var_8;
      var_8 = Det(mat_8);
      // step 9: binary operation '*'
      SIMD<double> var_9;
      var_9 = var_8 * var_8;
      // step 10: -0.333333
      SIMD<double> var_10;
      var_10 = -0x1.5555555555556p-2 /* (-3.3333333333333337e-01) */;
      // step 11: binary operation 'pow'
      SIMD<double> var_11;
      var_11 = pow(var_9,var_10);
      // step 12: scale 3
      SIMD<double> var_12;
      var_12 = (0x1.8p+1 /* (3.0000000000000000e+00) */ * var_11);
      // step 13: binary operation '+'
      SIMD<double> var_13;
      var_13 = var_7 + var_12;
      // step 14: 1
      SIMD<double> var_14;
      var_14 = 0x1p+0 /* (1.0000000000000000e+00) */;
      // step 15: binary operation '-'
      SIMD<double> var_15;
      var_15 = var_13 - var_14;
      // step 16: scale 43.75
      SIMD<double> var_16;
      var_16 = (0x1.5ep+5 /* (4.3750000000000000e+01) */ * var_15);
      SIMD<double> var_17;
      var_17 = var_16;
      results(0,i) =var_17;

    }
  }

  void CompiledEvaluateDeriv(BaseMappedIntegrationRule & mir, BareSliceMatrix<AutoDiff<1,double>> results ) {

    FlatMatrix<double> values_1;
    ProxyUserData * tmp_1_0 = (ProxyUserData*)mir.GetTransformation().userdata;
    {
      // if (!tmp_1_0)
      // throw Exception ("cannot evaluate ProxyFunction without userdata");
      if (tmp_1_0->fel) {
        auto x = tmp_1_0->GetMemory (reinterpret_cast<ProxyFunction*>(compiled_code_pointer50));
        values_1.AssignMemory(x.Height(), x.Width(), &x(0,0));
      }
    }
    [[maybe_unused]] const bool has_values_1 = tmp_1_0->HasMemory(reinterpret_cast<ProxyFunction*>(compiled_code_pointer50));
    AutoDiff<1,double> comp_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==0 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer50))
      comp_1_0_0.DValue(0) = 1.0;
    AutoDiff<1,double> comp_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==1 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer50))
      comp_1_0_1.DValue(0) = 1.0;
    AutoDiff<1,double> comp_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==2 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer50))
      comp_1_1_0.DValue(0) = 1.0;
    AutoDiff<1,double> comp_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==3 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer50))
      comp_1_1_1.DValue(0) = 1.0;

    [[maybe_unused]] auto points = mir.GetPoints();
    [[maybe_unused]] auto domain_index = mir.GetTransformation().GetElementIndex();
    for ( auto i : Range(mir)) {
      [[maybe_unused]] auto & ip = mir[i];
      // step 0: Identity matrix
      AutoDiff<1,double> var_0_0_0;
      AutoDiff<1,double> var_0_0_1;
      AutoDiff<1,double> var_0_1_0;
      AutoDiff<1,double> var_0_1_1;
      var_0_0_0 = 1.0;
      var_0_0_1 = 0.0;
      var_0_1_0 = 0.0;
      var_0_1_1 = 1.0;
      // step 1: trial-function diffop = grad
      AutoDiff<1,double> var_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_0 = 0.0;
      AutoDiff<1,double> var_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_1 = 0.0;
      AutoDiff<1,double> var_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_0 = 0.0;
      AutoDiff<1,double> var_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_1 = 0.0;
      // if (tmp_1_0->fel) {
      if (has_values_1) {
        var_1_0_0.Value() = values_1(i,0);
        var_1_0_1.Value() = values_1(i,1);
        var_1_1_0.Value() = values_1(i,2);
        var_1_1_1.Value() = values_1(i,3);
      }
      {
        var_1_0_0.DValue(0) = comp_1_0_0.DValue(0);
        var_1_0_1.DValue(0) = comp_1_0_1.DValue(0);
        var_1_1_0.DValue(0) = comp_1_1_0.DValue(0);
        var_1_1_1.DValue(0) = comp_1_1_1.DValue(0);
      }
      // step 2: binary operation '+'
      AutoDiff<1,double> var_2_0_0;
      AutoDiff<1,double> var_2_0_1;
      AutoDiff<1,double> var_2_1_0;
      AutoDiff<1,double> var_2_1_1;
      var_2_0_0 = var_0_0_0 + var_1_0_0;
      var_2_0_1 = var_0_0_1 + var_1_0_1;
      var_2_1_0 = var_0_1_0 + var_1_1_0;
      var_2_1_1 = var_0_1_1 + var_1_1_1;
      // step 3: Matrix transpose
      AutoDiff<1,double> var_3_0_0;
      AutoDiff<1,double> var_3_0_1;
      AutoDiff<1,double> var_3_1_0;
      AutoDiff<1,double> var_3_1_1;
      var_3_0_0 = var_2_0_0;
      var_3_0_1 = var_2_1_0;
      var_3_1_0 = var_2_0_1;
      var_3_1_1 = var_2_1_1;
      // step 4: matrix-matrix multiply
      AutoDiff<1,double> var_4_0_0;
      AutoDiff<1,double> var_4_0_1;
      AutoDiff<1,double> var_4_1_0;
      AutoDiff<1,double> var_4_1_1;
      var_4_0_0 = (((var_3_0_0 * var_2_0_0)) + (var_3_0_1 * var_2_1_0));
      var_4_0_1 = (((var_3_0_0 * var_2_0_1)) + (var_3_0_1 * var_2_1_1));
      var_4_1_0 = (((var_3_1_0 * var_2_0_0)) + (var_3_1_1 * var_2_1_0));
      var_4_1_1 = (((var_3_1_0 * var_2_0_1)) + (var_3_1_1 * var_2_1_1));
      // step 5: Identity matrix
      AutoDiff<1,double> var_5_0_0;
      AutoDiff<1,double> var_5_0_1;
      AutoDiff<1,double> var_5_1_0;
      AutoDiff<1,double> var_5_1_1;
      var_5_0_0 = 1.0;
      var_5_0_1 = 0.0;
      var_5_1_0 = 0.0;
      var_5_1_1 = 1.0;
      // step 6: binary operation '-'
      AutoDiff<1,double> var_6_0_0;
      AutoDiff<1,double> var_6_0_1;
      AutoDiff<1,double> var_6_1_0;
      AutoDiff<1,double> var_6_1_1;
      var_6_0_0 = var_4_0_0 - var_5_0_0;
      var_6_0_1 = var_4_0_1 - var_5_0_1;
      var_6_1_0 = var_4_1_0 - var_5_1_0;
      var_6_1_1 = var_4_1_1 - var_5_1_1;
      // step 7: trace
      AutoDiff<1,double> var_7;
      var_7 = ((var_6_0_0) + var_6_1_1);
      // step 8: Determinant
      Mat<2,2,AutoDiff<1,double>> mat_8;
      mat_8(0,0) = var_2_0_0;
      mat_8(0,1) = var_2_0_1;
      mat_8(1,0) = var_2_1_0;
      mat_8(1,1) = var_2_1_1;
      AutoDiff<1,double> var_8;
      var_8 = Det(mat_8);
      // step 9: binary operation '*'
      AutoDiff<1,double> var_9;
      var_9 = var_8 * var_8;
      // step 10: -0.333333
      AutoDiff<1,double> var_10;
      var_10 = -0x1.5555555555556p-2 /* (-3.3333333333333337e-01) */;
      // step 11: binary operation 'pow'
      AutoDiff<1,double> var_11;
      var_11 = pow(var_9,var_10);
      // step 12: scale 3
      AutoDiff<1,double> var_12;
      var_12 = (0x1.8p+1 /* (3.0000000000000000e+00) */ * var_11);
      // step 13: binary operation '+'
      AutoDiff<1,double> var_13;
      var_13 = var_7 + var_12;
      // step 14: 1
      AutoDiff<1,double> var_14;
      var_14 = 0x1p+0 /* (1.0000000000000000e+00) */;
      // step 15: binary operation '-'
      AutoDiff<1,double> var_15;
      var_15 = var_13 - var_14;
      // step 16: scale 43.75
      AutoDiff<1,double> var_16;
      var_16 = (0x1.5ep+5 /* (4.3750000000000000e+01) */ * var_15);
      AutoDiff<1,double> var_17;
      var_17 = var_16;
      results(i,0) =var_17;

    }
  }

  void CompiledEvaluateDerivSIMD(SIMD_BaseMappedIntegrationRule & mir, BareSliceMatrix<AutoDiff<1,SIMD<double>>> results ) {

    FlatMatrix<SIMD<double>> values_1;
    ProxyUserData * tmp_1_0 = (ProxyUserData*)mir.GetTransformation().userdata;
    {
      if (tmp_1_0->fel) {
        auto x = tmp_1_0->GetAMemory (reinterpret_cast<ProxyFunction*>(compiled_code_pointer51));
        values_1.AssignMemory(x.Height(), x.Width(), &x(0,0));
      }
    }
    [[maybe_unused]] const bool has_values_1 = tmp_1_0->HasMemory(reinterpret_cast<ProxyFunction*>(compiled_code_pointer51));
    AutoDiff<1,SIMD<double>> comp_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==0 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer51))
      comp_1_0_0.DValue(0) = 1.0;
    AutoDiff<1,SIMD<double>> comp_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==1 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer51))
      comp_1_0_1.DValue(0) = 1.0;
    AutoDiff<1,SIMD<double>> comp_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==2 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer51))
      comp_1_1_0.DValue(0) = 1.0;
    AutoDiff<1,SIMD<double>> comp_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(tmp_1_0->trial_comp==3 && tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer51))
      comp_1_1_1.DValue(0) = 1.0;

    [[maybe_unused]] auto points = mir.GetPoints();
    [[maybe_unused]] auto domain_index = mir.GetTransformation().GetElementIndex();
    for ( auto i : Range(mir)) {
      [[maybe_unused]] auto & ip = mir[i];
      // step 0: Identity matrix
      AutoDiff<1,SIMD<double>> var_0_0_0;
      AutoDiff<1,SIMD<double>> var_0_0_1;
      AutoDiff<1,SIMD<double>> var_0_1_0;
      AutoDiff<1,SIMD<double>> var_0_1_1;
      var_0_0_0 = 1.0;
      var_0_0_1 = 0.0;
      var_0_1_0 = 0.0;
      var_0_1_1 = 1.0;
      // step 1: trial-function diffop = grad
      AutoDiff<1,SIMD<double>> var_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_0 = 0.0;
      AutoDiff<1,SIMD<double>> var_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_1 = 0.0;
      AutoDiff<1,SIMD<double>> var_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_0 = 0.0;
      AutoDiff<1,SIMD<double>> var_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_1 = 0.0;
      // if (tmp_1_0->fel) {
      if (has_values_1) {
        var_1_0_0.Value() = values_1(0,i);
        var_1_0_1.Value() = values_1(1,i);
        var_1_1_0.Value() = values_1(2,i);
        var_1_1_1.Value() = values_1(3,i);
      }
      {
        var_1_0_0.DValue(0) = comp_1_0_0.DValue(0);
        var_1_0_1.DValue(0) = comp_1_0_1.DValue(0);
        var_1_1_0.DValue(0) = comp_1_1_0.DValue(0);
        var_1_1_1.DValue(0) = comp_1_1_1.DValue(0);
      }
      // step 2: binary operation '+'
      AutoDiff<1,SIMD<double>> var_2_0_0;
      AutoDiff<1,SIMD<double>> var_2_0_1;
      AutoDiff<1,SIMD<double>> var_2_1_0;
      AutoDiff<1,SIMD<double>> var_2_1_1;
      var_2_0_0 = var_0_0_0 + var_1_0_0;
      var_2_0_1 = var_0_0_1 + var_1_0_1;
      var_2_1_0 = var_0_1_0 + var_1_1_0;
      var_2_1_1 = var_0_1_1 + var_1_1_1;
      // step 3: Matrix transpose
      AutoDiff<1,SIMD<double>> var_3_0_0;
      AutoDiff<1,SIMD<double>> var_3_0_1;
      AutoDiff<1,SIMD<double>> var_3_1_0;
      AutoDiff<1,SIMD<double>> var_3_1_1;
      var_3_0_0 = var_2_0_0;
      var_3_0_1 = var_2_1_0;
      var_3_1_0 = var_2_0_1;
      var_3_1_1 = var_2_1_1;
      // step 4: matrix-matrix multiply
      AutoDiff<1,SIMD<double>> var_4_0_0;
      AutoDiff<1,SIMD<double>> var_4_0_1;
      AutoDiff<1,SIMD<double>> var_4_1_0;
      AutoDiff<1,SIMD<double>> var_4_1_1;
      var_4_0_0 = (((var_3_0_0 * var_2_0_0)) + (var_3_0_1 * var_2_1_0));
      var_4_0_1 = (((var_3_0_0 * var_2_0_1)) + (var_3_0_1 * var_2_1_1));
      var_4_1_0 = (((var_3_1_0 * var_2_0_0)) + (var_3_1_1 * var_2_1_0));
      var_4_1_1 = (((var_3_1_0 * var_2_0_1)) + (var_3_1_1 * var_2_1_1));
      // step 5: Identity matrix
      AutoDiff<1,SIMD<double>> var_5_0_0;
      AutoDiff<1,SIMD<double>> var_5_0_1;
      AutoDiff<1,SIMD<double>> var_5_1_0;
      AutoDiff<1,SIMD<double>> var_5_1_1;
      var_5_0_0 = 1.0;
      var_5_0_1 = 0.0;
      var_5_1_0 = 0.0;
      var_5_1_1 = 1.0;
      // step 6: binary operation '-'
      AutoDiff<1,SIMD<double>> var_6_0_0;
      AutoDiff<1,SIMD<double>> var_6_0_1;
      AutoDiff<1,SIMD<double>> var_6_1_0;
      AutoDiff<1,SIMD<double>> var_6_1_1;
      var_6_0_0 = var_4_0_0 - var_5_0_0;
      var_6_0_1 = var_4_0_1 - var_5_0_1;
      var_6_1_0 = var_4_1_0 - var_5_1_0;
      var_6_1_1 = var_4_1_1 - var_5_1_1;
      // step 7: trace
      AutoDiff<1,SIMD<double>> var_7;
      var_7 = ((var_6_0_0) + var_6_1_1);
      // step 8: Determinant
      Mat<2,2,AutoDiff<1,SIMD<double>>> mat_8;
      mat_8(0,0) = var_2_0_0;
      mat_8(0,1) = var_2_0_1;
      mat_8(1,0) = var_2_1_0;
      mat_8(1,1) = var_2_1_1;
      AutoDiff<1,SIMD<double>> var_8;
      var_8 = Det(mat_8);
      // step 9: binary operation '*'
      AutoDiff<1,SIMD<double>> var_9;
      var_9 = var_8 * var_8;
      // step 10: -0.333333
      AutoDiff<1,SIMD<double>> var_10;
      var_10 = -0x1.5555555555556p-2 /* (-3.3333333333333337e-01) */;
      // step 11: binary operation 'pow'
      AutoDiff<1,SIMD<double>> var_11;
      var_11 = pow(var_9,var_10);
      // step 12: scale 3
      AutoDiff<1,SIMD<double>> var_12;
      var_12 = (0x1.8p+1 /* (3.0000000000000000e+00) */ * var_11);
      // step 13: binary operation '+'
      AutoDiff<1,SIMD<double>> var_13;
      var_13 = var_7 + var_12;
      // step 14: 1
      AutoDiff<1,SIMD<double>> var_14;
      var_14 = 0x1p+0 /* (1.0000000000000000e+00) */;
      // step 15: binary operation '-'
      AutoDiff<1,SIMD<double>> var_15;
      var_15 = var_13 - var_14;
      // step 16: scale 43.75
      AutoDiff<1,SIMD<double>> var_16;
      var_16 = (0x1.5ep+5 /* (4.3750000000000000e+01) */ * var_15);
      AutoDiff<1,SIMD<double>> var_17;
      var_17 = var_16;
      results(0,i) =var_17;

    }
  }

  void CompiledEvaluateDDeriv(BaseMappedIntegrationRule & mir, BareSliceMatrix<AutoDiffDiff<1,double>> results ) {

    FlatMatrix<double> values_1;
    ProxyUserData * tmp_1_0 = (ProxyUserData*)mir.GetTransformation().userdata;
    {
      if (tmp_1_0->fel) {
        auto x = tmp_1_0->GetMemory (reinterpret_cast<ProxyFunction*>(compiled_code_pointer52));
        values_1.AssignMemory(x.Height(), x.Width(), &x(0,0));
      }
    }
    [[maybe_unused]] const bool has_values_1 = tmp_1_0->HasMemory(reinterpret_cast<ProxyFunction*>(compiled_code_pointer52));
    AutoDiffDiff<1,double> comp_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(( (tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer52)) && (tmp_1_0->trial_comp==0))
       ||  ((tmp_1_0->testfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer52)) && (tmp_1_0->test_comp==0)))
      comp_1_0_0.DValue(0) = 1.0;
    AutoDiffDiff<1,double> comp_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(( (tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer52)) && (tmp_1_0->trial_comp==1))
       ||  ((tmp_1_0->testfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer52)) && (tmp_1_0->test_comp==1)))
      comp_1_0_1.DValue(0) = 1.0;
    AutoDiffDiff<1,double> comp_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(( (tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer52)) && (tmp_1_0->trial_comp==2))
       ||  ((tmp_1_0->testfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer52)) && (tmp_1_0->test_comp==2)))
      comp_1_1_0.DValue(0) = 1.0;
    AutoDiffDiff<1,double> comp_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(( (tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer52)) && (tmp_1_0->trial_comp==3))
       ||  ((tmp_1_0->testfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer52)) && (tmp_1_0->test_comp==3)))
      comp_1_1_1.DValue(0) = 1.0;

    [[maybe_unused]] auto points = mir.GetPoints();
    [[maybe_unused]] auto domain_index = mir.GetTransformation().GetElementIndex();
    for ( auto i : Range(mir)) {
      [[maybe_unused]] auto & ip = mir[i];
      // step 0: Identity matrix
      AutoDiffDiff<1,double> var_0_0_0;
      AutoDiffDiff<1,double> var_0_0_1;
      AutoDiffDiff<1,double> var_0_1_0;
      AutoDiffDiff<1,double> var_0_1_1;
      var_0_0_0 = 1.0;
      var_0_0_1 = 0.0;
      var_0_1_0 = 0.0;
      var_0_1_1 = 1.0;
      // step 1: trial-function diffop = grad
      AutoDiffDiff<1,double> var_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_0 = 0.0;
      AutoDiffDiff<1,double> var_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_1 = 0.0;
      AutoDiffDiff<1,double> var_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_0 = 0.0;
      AutoDiffDiff<1,double> var_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_1 = 0.0;
      // if (tmp_1_0->fel) {
      if (has_values_1) {
        var_1_0_0.Value() = values_1(i,0);
        var_1_0_1.Value() = values_1(i,1);
        var_1_1_0.Value() = values_1(i,2);
        var_1_1_1.Value() = values_1(i,3);
      }
      {
        var_1_0_0.DValue(0) = comp_1_0_0.DValue(0);
        var_1_0_1.DValue(0) = comp_1_0_1.DValue(0);
        var_1_1_0.DValue(0) = comp_1_1_0.DValue(0);
        var_1_1_1.DValue(0) = comp_1_1_1.DValue(0);
      }
      // step 2: binary operation '+'
      AutoDiffDiff<1,double> var_2_0_0;
      AutoDiffDiff<1,double> var_2_0_1;
      AutoDiffDiff<1,double> var_2_1_0;
      AutoDiffDiff<1,double> var_2_1_1;
      var_2_0_0 = var_0_0_0 + var_1_0_0;
      var_2_0_1 = var_0_0_1 + var_1_0_1;
      var_2_1_0 = var_0_1_0 + var_1_1_0;
      var_2_1_1 = var_0_1_1 + var_1_1_1;
      // step 3: Matrix transpose
      AutoDiffDiff<1,double> var_3_0_0;
      AutoDiffDiff<1,double> var_3_0_1;
      AutoDiffDiff<1,double> var_3_1_0;
      AutoDiffDiff<1,double> var_3_1_1;
      var_3_0_0 = var_2_0_0;
      var_3_0_1 = var_2_1_0;
      var_3_1_0 = var_2_0_1;
      var_3_1_1 = var_2_1_1;
      // step 4: matrix-matrix multiply
      AutoDiffDiff<1,double> var_4_0_0;
      AutoDiffDiff<1,double> var_4_0_1;
      AutoDiffDiff<1,double> var_4_1_0;
      AutoDiffDiff<1,double> var_4_1_1;
      var_4_0_0 = (((var_3_0_0 * var_2_0_0)) + (var_3_0_1 * var_2_1_0));
      var_4_0_1 = (((var_3_0_0 * var_2_0_1)) + (var_3_0_1 * var_2_1_1));
      var_4_1_0 = (((var_3_1_0 * var_2_0_0)) + (var_3_1_1 * var_2_1_0));
      var_4_1_1 = (((var_3_1_0 * var_2_0_1)) + (var_3_1_1 * var_2_1_1));
      // step 5: Identity matrix
      AutoDiffDiff<1,double> var_5_0_0;
      AutoDiffDiff<1,double> var_5_0_1;
      AutoDiffDiff<1,double> var_5_1_0;
      AutoDiffDiff<1,double> var_5_1_1;
      var_5_0_0 = 1.0;
      var_5_0_1 = 0.0;
      var_5_1_0 = 0.0;
      var_5_1_1 = 1.0;
      // step 6: binary operation '-'
      AutoDiffDiff<1,double> var_6_0_0;
      AutoDiffDiff<1,double> var_6_0_1;
      AutoDiffDiff<1,double> var_6_1_0;
      AutoDiffDiff<1,double> var_6_1_1;
      var_6_0_0 = var_4_0_0 - var_5_0_0;
      var_6_0_1 = var_4_0_1 - var_5_0_1;
      var_6_1_0 = var_4_1_0 - var_5_1_0;
      var_6_1_1 = var_4_1_1 - var_5_1_1;
      // step 7: trace
      AutoDiffDiff<1,double> var_7;
      var_7 = ((var_6_0_0) + var_6_1_1);
      // step 8: Determinant
      Mat<2,2,AutoDiffDiff<1,double>> mat_8;
      mat_8(0,0) = var_2_0_0;
      mat_8(0,1) = var_2_0_1;
      mat_8(1,0) = var_2_1_0;
      mat_8(1,1) = var_2_1_1;
      AutoDiffDiff<1,double> var_8;
      var_8 = Det(mat_8);
      // step 9: binary operation '*'
      AutoDiffDiff<1,double> var_9;
      var_9 = var_8 * var_8;
      // step 10: -0.333333
      AutoDiffDiff<1,double> var_10;
      var_10 = -0x1.5555555555556p-2 /* (-3.3333333333333337e-01) */;
      // step 11: binary operation 'pow'
      AutoDiffDiff<1,double> var_11;
      var_11 = pow(var_9,var_10);
      // step 12: scale 3
      AutoDiffDiff<1,double> var_12;
      var_12 = (0x1.8p+1 /* (3.0000000000000000e+00) */ * var_11);
      // step 13: binary operation '+'
      AutoDiffDiff<1,double> var_13;
      var_13 = var_7 + var_12;
      // step 14: 1
      AutoDiffDiff<1,double> var_14;
      var_14 = 0x1p+0 /* (1.0000000000000000e+00) */;
      // step 15: binary operation '-'
      AutoDiffDiff<1,double> var_15;
      var_15 = var_13 - var_14;
      // step 16: scale 43.75
      AutoDiffDiff<1,double> var_16;
      var_16 = (0x1.5ep+5 /* (4.3750000000000000e+01) */ * var_15);
      AutoDiffDiff<1,double> var_17;
      var_17 = var_16;
      results(i,0) =var_17;

    }
  }

  void CompiledEvaluateDDerivSIMD(SIMD_BaseMappedIntegrationRule & mir, BareSliceMatrix<AutoDiffDiff<1,SIMD<double>>> results ) {

    FlatMatrix<SIMD<double>> values_1;
    ProxyUserData * tmp_1_0 = (ProxyUserData*)mir.GetTransformation().userdata;
    {
      if (tmp_1_0->fel) {
        auto x = tmp_1_0->GetAMemory (reinterpret_cast<ProxyFunction*>(compiled_code_pointer53));
        values_1.AssignMemory(x.Height(), x.Width(), &x(0,0));
      }
    }
    [[maybe_unused]] const bool has_values_1 = tmp_1_0->HasMemory(reinterpret_cast<ProxyFunction*>(compiled_code_pointer53));
    AutoDiffDiff<1,SIMD<double>> comp_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(( (tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer53)) && (tmp_1_0->trial_comp==0))
       ||  ((tmp_1_0->testfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer53)) && (tmp_1_0->test_comp==0)))
      comp_1_0_0.DValue(0) = 1.0;
    AutoDiffDiff<1,SIMD<double>> comp_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(( (tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer53)) && (tmp_1_0->trial_comp==1))
       ||  ((tmp_1_0->testfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer53)) && (tmp_1_0->test_comp==1)))
      comp_1_0_1.DValue(0) = 1.0;
    AutoDiffDiff<1,SIMD<double>> comp_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
    if(( (tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer53)) && (tmp_1_0->trial_comp==2))
       ||  ((tmp_1_0->testfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer53)) && (tmp_1_0->test_comp==2)))
      comp_1_1_0.DValue(0) = 1.0;
    AutoDiffDiff<1,SIMD<double>> comp_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
    if(( (tmp_1_0->trialfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer53)) && (tmp_1_0->trial_comp==3))
       ||  ((tmp_1_0->testfunction == reinterpret_cast<ProxyFunction*>(compiled_code_pointer53)) && (tmp_1_0->test_comp==3)))
      comp_1_1_1.DValue(0) = 1.0;

    [[maybe_unused]] auto points = mir.GetPoints();
    [[maybe_unused]] auto domain_index = mir.GetTransformation().GetElementIndex();
    for ( auto i : Range(mir)) {
      [[maybe_unused]] auto & ip = mir[i];
      // step 0: Identity matrix
      AutoDiffDiff<1,SIMD<double>> var_0_0_0;
      AutoDiffDiff<1,SIMD<double>> var_0_0_1;
      AutoDiffDiff<1,SIMD<double>> var_0_1_0;
      AutoDiffDiff<1,SIMD<double>> var_0_1_1;
      var_0_0_0 = 1.0;
      var_0_0_1 = 0.0;
      var_0_1_0 = 0.0;
      var_0_1_1 = 1.0;
      // step 1: trial-function diffop = grad
      AutoDiffDiff<1,SIMD<double>> var_1_0_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_0 = 0.0;
      AutoDiffDiff<1,SIMD<double>> var_1_0_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_0_1 = 0.0;
      AutoDiffDiff<1,SIMD<double>> var_1_1_0(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_0 = 0.0;
      AutoDiffDiff<1,SIMD<double>> var_1_1_1(0x0p+0 /* (0.0000000000000000e+00) */);
      var_1_1_1 = 0.0;
      if (has_values_1) {
        var_1_0_0.Value() = values_1(0,i);
        var_1_0_1.Value() = values_1(1,i);
        var_1_1_0.Value() = values_1(2,i);
        var_1_1_1.Value() = values_1(3,i);
      }
      {
        var_1_0_0.DValue(0) = comp_1_0_0.DValue(0);
        var_1_0_1.DValue(0) = comp_1_0_1.DValue(0);
        var_1_1_0.DValue(0) = comp_1_1_0.DValue(0);
        var_1_1_1.DValue(0) = comp_1_1_1.DValue(0);
      }
      // step 2: binary operation '+'
      AutoDiffDiff<1,SIMD<double>> var_2_0_0;
      AutoDiffDiff<1,SIMD<double>> var_2_0_1;
      AutoDiffDiff<1,SIMD<double>> var_2_1_0;
      AutoDiffDiff<1,SIMD<double>> var_2_1_1;
      var_2_0_0 = var_0_0_0 + var_1_0_0;
      var_2_0_1 = var_0_0_1 + var_1_0_1;
      var_2_1_0 = var_0_1_0 + var_1_1_0;
      var_2_1_1 = var_0_1_1 + var_1_1_1;
      // step 3: Matrix transpose
      AutoDiffDiff<1,SIMD<double>> var_3_0_0;
      AutoDiffDiff<1,SIMD<double>> var_3_0_1;
      AutoDiffDiff<1,SIMD<double>> var_3_1_0;
      AutoDiffDiff<1,SIMD<double>> var_3_1_1;
      var_3_0_0 = var_2_0_0;
      var_3_0_1 = var_2_1_0;
      var_3_1_0 = var_2_0_1;
      var_3_1_1 = var_2_1_1;
      // step 4: matrix-matrix multiply
      AutoDiffDiff<1,SIMD<double>> var_4_0_0;
      AutoDiffDiff<1,SIMD<double>> var_4_0_1;
      AutoDiffDiff<1,SIMD<double>> var_4_1_0;
      AutoDiffDiff<1,SIMD<double>> var_4_1_1;
      var_4_0_0 = (((var_3_0_0 * var_2_0_0)) + (var_3_0_1 * var_2_1_0));
      var_4_0_1 = (((var_3_0_0 * var_2_0_1)) + (var_3_0_1 * var_2_1_1));
      var_4_1_0 = (((var_3_1_0 * var_2_0_0)) + (var_3_1_1 * var_2_1_0));
      var_4_1_1 = (((var_3_1_0 * var_2_0_1)) + (var_3_1_1 * var_2_1_1));
      // step 5: Identity matrix
      AutoDiffDiff<1,SIMD<double>> var_5_0_0;
      AutoDiffDiff<1,SIMD<double>> var_5_0_1;
      AutoDiffDiff<1,SIMD<double>> var_5_1_0;
      AutoDiffDiff<1,SIMD<double>> var_5_1_1;
      var_5_0_0 = 1.0;
      var_5_0_1 = 0.0;
      var_5_1_0 = 0.0;
      var_5_1_1 = 1.0;
      // step 6: binary operation '-'
      AutoDiffDiff<1,SIMD<double>> var_6_0_0;
      AutoDiffDiff<1,SIMD<double>> var_6_0_1;
      AutoDiffDiff<1,SIMD<double>> var_6_1_0;
      AutoDiffDiff<1,SIMD<double>> var_6_1_1;
      var_6_0_0 = var_4_0_0 - var_5_0_0;
      var_6_0_1 = var_4_0_1 - var_5_0_1;
      var_6_1_0 = var_4_1_0 - var_5_1_0;
      var_6_1_1 = var_4_1_1 - var_5_1_1;
      // step 7: trace
      AutoDiffDiff<1,SIMD<double>> var_7;
      var_7 = ((var_6_0_0) + var_6_1_1);
      // step 8: Determinant
      Mat<2,2,AutoDiffDiff<1,SIMD<double>>> mat_8;
      mat_8(0,0) = var_2_0_0;
      mat_8(0,1) = var_2_0_1;
      mat_8(1,0) = var_2_1_0;
      mat_8(1,1) = var_2_1_1;
      AutoDiffDiff<1,SIMD<double>> var_8;
      var_8 = Det(mat_8);
      // step 9: binary operation '*'
      AutoDiffDiff<1,SIMD<double>> var_9;
      var_9 = var_8 * var_8;
      // step 10: -0.333333
      AutoDiffDiff<1,SIMD<double>> var_10;
      var_10 = -0x1.5555555555556p-2 /* (-3.3333333333333337e-01) */;
      // step 11: binary operation 'pow'
      AutoDiffDiff<1,SIMD<double>> var_11;
      var_11 = pow(var_9,var_10);
      // step 12: scale 3
      AutoDiffDiff<1,SIMD<double>> var_12;
      var_12 = (0x1.8p+1 /* (3.0000000000000000e+00) */ * var_11);
      // step 13: binary operation '+'
      AutoDiffDiff<1,SIMD<double>> var_13;
      var_13 = var_7 + var_12;
      // step 14: 1
      AutoDiffDiff<1,SIMD<double>> var_14;
      var_14 = 0x1p+0 /* (1.0000000000000000e+00) */;
      // step 15: binary operation '-'
      AutoDiffDiff<1,SIMD<double>> var_15;
      var_15 = var_13 - var_14;
      // step 16: scale 43.75
      AutoDiffDiff<1,SIMD<double>> var_16;
      var_16 = (0x1.5ep+5 /* (4.3750000000000000e+01) */ * var_15);
      AutoDiffDiff<1,SIMD<double>> var_17;
      var_17 = var_16;
      results(0,i) =var_17;

    }
  }

}
```